In [0]:
# 과제 8

In [0]:
peopleDF = spark.read.parquet("/mnt/training/dataframes/people-10m.parquet")
peopleDF.show(5)

+---+---------+----------+----------+------+-------------------+-----------+------+
 id|firstName|middleName| lastName|gender| birthDate| ssn|salary|
+---+---------+----------+----------+------+-------------------+-----------+------+
 1| Pennie| Carry|Hirschmann| F|1955-07-02 04:00:00|981-43-9345| 56172|
 2| An| Amira| Cowper| F|1992-02-08 05:00:00|978-97-8086| 40203|
 3| Quyen| Marlen| Dome| F|1970-10-11 04:00:00|957-57-8246| 53417|
 4| Coralie| Antonina| Marshal| F|1990-04-11 04:00:00|963-39-4885| 94727|
 5| Terrie| Wava| Bonar| F|1980-01-16 05:00:00|964-49-8051| 79908|
+---+---------+----------+----------+------+-------------------+-----------+------+
only showing top 5 rows

In [0]:
peopleDF.select('gender', 'salary').show(5)

+------+------+
gender|salary|
+------+------+
 F| 56172|
 F| 40203|
 F| 53417|
 F| 94727|
 F| 79908|
+------+------+
only showing top 5 rows

In [0]:
from pyspark.sql.functions import year
peopleDF = peopleDF.select('lastName', 'salary', 'birthDate').filter("gender='M'" and year("birthDate")> "1990")
peopleDF.show(5)

+-----------+------+-------------------+
 lastName|salary| birthDate|
+-----------+------+-------------------+
 Cowper| 40203|1992-02-08 05:00:00|
 Cardon| 60449|1994-05-15 04:00:00|
 Goldring| 73060|1997-07-09 04:00:00|
Pendleberry| 60857|1998-12-02 05:00:00|
 Lyfe|101601|1994-06-23 04:00:00|
+-----------+------+-------------------+
only showing top 5 rows

In [0]:
#과제 9

In [0]:
peopleDF = spark.read.parquet("/mnt/training/dataframes/people-10m.parquet")
from pyspark.sql.functions import col
dordonDF = peopleDF.\
              select(year("birthDate").alias("birthYear"), "firstName"). \
              filter((col("firstName")=='Donna') | (col("firstName")=='Dorothy')).\
              filter("gender == 'F'").\
              groupBy('birthYear', 'firstName').\
              count()
dordonDF.show(5)

+---------+---------+-----+
birthYear|firstName|count|
+---------+---------+-----+
 1999| Donna| 22|
 1979| Donna| 30|
 1978| Dorothy| 31|
 1982| Donna| 24|
 1985| Donna| 27|
+---------+---------+-----+
only showing top 5 rows

In [0]:
peopleDF = spark.read.parquet("/mnt/training/dataframes/people-10m.parquet")
from pyspark.sql.functions import col
dordonDF = peopleDF.\
              select(year("birthDate").alias("birthYear"), "firstName"). \
              filter((col("firstName")=='Donna') | (col("firstName")=='Dorothy')).\
              filter("gender == 'F'").\
              groupBy('birthYear', 'firstName').\
              count()

dordonDF.orderBy('birthYear').show(5)

+---------+---------+-----+
birthYear|firstName|count|
+---------+---------+-----+
 1952| Donna| 24|
 1952| Dorothy| 21|
 1953| Donna| 37|
 1953| Dorothy| 38|
 1954| Donna| 32|
+---------+---------+-----+
only showing top 5 rows

In [0]:
dordonDF = peopleDF.\
              select(year("birthDate").alias("birthYear"), "firstName"). \
              filter((col("firstName")=='Donna') | (col("firstName")=='Dorothy')).\
              filter("gender == 'F'").\
              filter(year("birthdate")>1990).\
              groupBy('birthYear', 'firstName').\
              count()

dordonDF = dordonDF.orderBy('birthYear')

In [0]:
display(dordonDF)

birthYear firstName count 1991 Dorothy 25 1991 Donna 27 1992 Dorothy 39 1992 Donna 30 1993 Donna 22 1993 Dorothy 28 1994 Donna 26 1994 Dorothy 21 1995 Dorothy 26 1995 Donna 33 1996 Dorothy 19 1996 Donna 23 1997 Dorothy 24 1997 Donna 36 1998 Donna 28 1998 Dorothy 33 1999 Donna 22 1999 Dorothy 25 2000 Dorothy 4 2000 Donna 2

In [0]:
from pyspark.sql.functions import count, desc
top10MaleFirstNameDF = peopleDF.\
        select("firstName").\
        filter("gender = 'M'").\
        groupBy("firstName").\
        agg(count(col('firstName')).alias('total')).\
        orderBy(desc('total')).\
        limit(10)

top10MaleFirstNameDF.show(5)

+---------+-----+
firstName|total|
+---------+-----+
 Marcelo| 4197|
 Reynaldo| 4193|
 Jeffrey| 4177|
 Sammie| 4170|
 Troy| 4167|
+---------+-----+
only showing top 5 rows

In [0]:
top10MaleFirstNameDF.createOrReplaceTempView("top10MaleFirstName")
resultsDF = spark.sql("select * from top10MaleFirstName order by firstName")
display(resultsDF)

firstName total Darin 4166 Fritz 4157 Jeffrey 4177 Jess 4153 Marcelo 4197 Reynaldo 4193 Sammie 4170 Tomas 4161 Troy 4167 Wyatt 4159

In [0]:
# 과제 10

In [0]:
bikeSharingDayDF = (spark
  .read                                                
  .option("inferSchema","true")                       
  .option("header","true")                             
  .csv("/mnt/training/bikeSharing/data-001/day.csv"))  
bikeSharingDayDF.show(3)

+-------+-------------------+------+---+----+-------+-------+----------+----------+--------+--------+--------+---------+------+----------+----+
instant| dteday|season| yr|mnth|holiday|weekday|workingday|weathersit| temp| atemp| hum|windspeed|casual|registered| cnt|
+-------+-------------------+------+---+----+-------+-------+----------+----------+--------+--------+--------+---------+------+----------+----+
 1|2011-01-01 00:00:00| 1| 0| 1| 0| 6| 0| 2|0.344167|0.363625|0.805833| 0.160446| 331| 654| 985|
 2|2011-01-02 00:00:00| 1| 0| 1| 0| 0| 0| 2|0.363478|0.353739|0.696087| 0.248539| 131| 670| 801|
 3|2011-01-03 00:00:00| 1| 0| 1| 0| 1| 1| 1|0.196364|0.189405|0.437273| 0.248309| 120| 1229|1349|
+-------+-------------------+------+---+----+-------+-------+----------+----------+--------+--------+--------+---------+------+----------+----+
only showing top 3 rows

In [0]:
databricksBlogDF = spark.read\
                        .option("inferSchema","true")\
                        .option("header","true")\
                        .json("/mnt/training/databricks-blog.json")

In [0]:
databricksBlogDF.printSchema()

root
-- authors: array (nullable = true)
 |-- element: string (containsNull = true)
-- categories: array (nullable = true)
 |-- element: string (containsNull = true)
-- content: string (nullable = true)
-- creator: string (nullable = true)
-- dates: struct (nullable = true)
 |-- createdOn: string (nullable = true)
 |-- publishedOn: string (nullable = true)
 |-- tz: string (nullable = true)
-- description: string (nullable = true)
-- id: long (nullable = true)
-- link: string (nullable = true)
-- slug: string (nullable = true)
-- status: string (nullable = true)
-- title: string (nullable = true)

In [0]:
from pyspark.sql.functions import lower, month, col, lit, date_format,to_date
BlogDF2 = databricksBlogDF.select('authors', 'categories', 'creator', 'dates')\
                          .withColumn("publishedOn",date_format(col("dates.publishedOn"), "yyyy"))
BlogDF2.show(3)

+--------------------+--------------------+-------+--------------------+-----------+
 authors| categories|creator| dates|publishedOn|
+--------------------+--------------------+-------+--------------------+-----------+
[Tomer Shiran (VP...|[Company Blog, Pa...| roy|[2014-04-10, 2014...| 2014|
 [Tathagata Das]|[Apache Spark, En...| tdas|[2014-04-10, 2014...| 2014|
 [Steven Hillion]|[Company Blog, Pa...| roy|[2014-04-01, 2014...| 2014|
+--------------------+--------------------+-------+--------------------+-----------+
only showing top 3 rows

In [0]:
resultDF = databricksBlogDF.select('categories', 'creator', to_date(col("dates.publishedOn")).alias('date'))\
                            .filter(year(col("date"))=='2013')\
                            .orderBy(col("date"))

resultDF.show(3)

+--------------------+-------+----------+
 categories|creator| date|
+--------------------+-------+----------+
[Announcements, C...| ion|2013-10-27|
[Announcements, C...| matei|2013-10-28|
[Company Blog, Pa...| ion|2013-10-29|
+--------------------+-------+----------+
only showing top 3 rows

In [0]:
from pyspark.sql.functions import explode, size
databricksBlog2DF = databricksBlogDF.\
  select('title', 'authors', explode(col('authors')).alias('author')).\
  filter(size(col('authors'))>1).\
  orderBy('title')
databricksBlog2DF.show(5)

+--------------------+--------------------+---------------+
 title| authors| author|
+--------------------+--------------------+---------------+
"Learning Spark" ...|[Holden Karau, An...|Patrick Wendell|
"Learning Spark" ...|[Holden Karau, An...| Matei Zaharia|
"Learning Spark" ...|[Holden Karau, An...| Andy Konwinski|
"Learning Spark" ...|[Holden Karau, An...| Holden Karau|
AMPLab updates th...|[Ahir Reddy, Reyn...| Ahir Reddy|
+--------------------+--------------------+---------------+
only showing top 5 rows

In [0]:
# 과제 11

In [0]:
%sql
CREATE TABLE IF NOT EXISTS fireIncidents
USING csv
OPTIONS (
  header "true",
  path "/mnt/davis/fire-incidents/fire-incidents-2016.csv",
  inferSchema "true"
)

In [0]:
%sql
SELECT `Incident Number` 
FROM fireIncidents 
WHERE `Incident Date` = '04/04/2016' or `Incident Date` = '09/27/2016'

Incident Number 16037478 16037483 16037484 16037492 16037503 16037505 16037508 16037530 16037540 16037541 16037543 16037546 16037549 16037551 16037553 16037554 16037555 16037566 16037573 16037574 16037580 16037582 16037588 16037589 16037591 16037593 16037592 16037595 16037599 16037608 16037607 16037617 16037628 16037635 16037640 16037643 16037658 16037662 16037674 16037681 16037682 16037684 16037688 16037699 16037700 16037701 16037706 16037711 16037721 16037725 16037726 16037729 16037730 16037734 16037741 16037743 16037749 16037751 16037754 16037756 16037759 16037775 16037776 16037780 16037782 16037785 16037788 16037792 16037793 16037799 16037800 16037805 16037809 16037808 16037813 16037817 16037821 16037826 16037831 16037838 16107245 16107249 16107251 16107261 16107280 16107281 16107282 16107297 16107304 16107305 16107313 16107320 16107325 16107327 16107328 16107332 16107333 16107338 16107341 16107347 16107351 16107356 16107357 16107368 16107369 16107372 16107374 16107380 16107381 16107384 16107385 16107386 16107387 16107391 16107392 16107399 16107403 16107404 16107406 16107412 16107414 16107417 16107418 16107420 16107425 16107427 16107433 16107439 16107450 16107460 16107468 16107471 16107474 16107478 16107477 16107482 16107483 16107486 16107509 16107518 16107521 16107525 16107537 16107533 16107535 16107539 16107549 16107550 16107553 16107555 16107556 16107559 16107561 16107568 16107576 16107577 16107581 16107590 16107600 16107604

In [0]:
%sql
select `Ignition Cause`, count(`Ignition Cause`) as count 
from fireIncidents
GROUP BY `Ignition Cause`
ORDER BY count DESC

Ignition Cause count 2 unintentional 561 1 intentional 223 u cause undetermined after investigation 156 3 failure of equipment or heat source 100 5 cause under investigation 35 4 act of nature 5 0 cause, other (only used for additional exposures) 1 null 0

In [0]:
%sql
CREATE TABLE IF NOT EXISTS fireCalls
USING csv
OPTIONS (
  header "true",
  path "/mnt/davis/fire-calls/fire-calls-truncated-comma.csv",
  inferSchema "true"
)

In [0]:
%sql
SELECT count(*)
FROM fireIncidents

count(1) 31771

In [0]:
%sql
SELECT count(*)
FROM fireCalls

count(1) 240613

In [0]:
%sql
SELECT /*+BROADCAST(fireCalls)*/ *
FROM fireCalls
JOIN fireIncidents on fireCalls.`Battalion` = fireIncidents.`Battalion`

Call Number Unit ID Incident Number Call Type Call Date Watch Date Received DtTm Entry DtTm Dispatch DtTm Response DtTm On Scene DtTm Transport DtTm Hospital DtTm Call Final Disposition Available DtTm Address City Zipcode of Incident Battalion Station Area Box Original Priority Priority Final Priority ALS Unit Call Type Group Number of Alarms Unit Type Unit sequence in call dispatch Fire Prevention District Supervisor District Neighborhooods - Analysis Boundaries Location RowID Incident Number Exposure Number Address Incident Date Call Number Alarm DtTm Arrival DtTm Close DtTm City Zipcode Battalion Station Area Box Suppression Units Suppression Personnel EMS Units EMS Personnel Other Units Other Personnel First Unit On Scene Estimated Property Loss Estimated Contents Loss Fire Fatalities Fire Injuries Civilian Fatalities Civilian Injuries Number of Alarms Primary Situation Mutual Aid Action Taken Primary Action Taken Secondary Action Taken Other Detector Alerted Occupants Property Use Area of Fire Origin Ignition Cause Ignition Factor Primary Ignition Factor Secondary Heat Source Item First Ignited Human Factors Associated with Ignition Structure Type Structure Status Floor of Fire Origin Fire Spread No Flame Spead Number of floors with minimum damage Number of floors with significant damage Number of floors with heavy damage Number of floors with extreme damage Detectors Present Detector Type Detector Operation Detector Effectiveness Detector Failure Reason Automatic Extinguishing System Present Automatic Extinguishing Sytem Type Automatic Extinguishing Sytem Perfomance Automatic Extinguishing Sytem Failure Reason Number of Sprinkler Heads Operating Supervisor District Neighborhood District Location 183031158 55 18126991 Medical Incident 10/30/2018 10/30/2018 10/30/2018 09:46:06 AM 10/30/2018 09:49:47 AM 10/30/2018 10:14:00 AM 10/30/2018 10:14:20 AM 10/30/2018 10:23:52 AM null null Patient Declined Transport 10/30/2018 10:49:00 AM 2900 Block of FOLSOM ST San Francisco 94110 B06 07 5614 2 2 2 true Non Life-threatening 1 MEDIC 2 6 9 Mission (37.7501075458546, -122.41377922888809) 183031158-55 16000003 0 Precita Av/florida Street 01/01/2016 160010015 01/01/2016 12:02:57 AM 01/01/2016 12:08:05 AM 01/01/2016 12:12:51 AM San Francisco 94110 B06 9 5621 1 4 0 0 0 0 null null null 0 0 0 0 null 600 good intent call, other n none 86 investigate null null null 962 residential street, road or residential driveway null null null null null null null null null null null na null null null null null null null null null null null null null null 9 Bernal Heights (37.7475540000296, -122.409572) 183030813 AM102 18126961 Medical Incident 10/30/2018 10/30/2018 10/30/2018 08:25:54 AM 10/30/2018 08:27:36 AM 10/30/2018 08:28:06 AM 10/30/2018 08:28:35 AM 10/30/2018 08:28:35 AM 10/30/2018 09:11:05 AM 10/30/2018 09:26:37 AM Code 2 Transport 10/30/2018 09:53:55 AM 1400 Block of TREAT WAY San Francisco 94110 B06 09 5622 2 2 2 false Potentially Life-Threatening 1 PRIVATE 1 6 9 Mission (37.74866782148175, -122.41254969224403) 183030813-AM102 16000003 0 Precita Av/florida Street 01/01/2016 160010015 01/01/2016 12:02:57 AM 01/01/2016 12:08:05 AM 01/01/2016 12:12:51 AM San Francisco 94110 B06 9 5621 1 4 0 0 0 0 null null null 0 0 0 0 null 600 good intent call, other n none 86 investigate null null null 962 residential street, road or residential driveway null null null null null null null null null null null na null null null null null null null null null null null null null null 9 Bernal Heights (37.7475540000296, -122.409572) 183030059 E11 18126895 Medical Incident 10/30/2018 10/29/2018 10/30/2018 12:45:35 AM 10/30/2018 12:46:58 AM 10/30/2018 12:47:46 AM 10/30/2018 12:49:08 AM 10/30/2018 12:51:46 AM null null No Merit 10/30/2018 12:52:07 AM 100 Block of VICKSBURG ST San Francisco 94114 B06 11 5514 3 3 3 true Non Life-threatening 1 ENGINE 1 6 8 Noe Valley (37.75280788414114, -122.42858598584684) 183030059-E11 16000003 0 Precita Av/florida Street 01/01/2016 160

In [0]:
%sql
SELECT /*+BROADCAST(fireIncidents)*/ *
FROM fireIncidents
JOIN fireCalls on fireCalls.`Battalion` = fireIncidents.`Battalion`

Incident Number Exposure Number Address Incident Date Call Number Alarm DtTm Arrival DtTm Close DtTm City Zipcode Battalion Station Area Box Suppression Units Suppression Personnel EMS Units EMS Personnel Other Units Other Personnel First Unit On Scene Estimated Property Loss Estimated Contents Loss Fire Fatalities Fire Injuries Civilian Fatalities Civilian Injuries Number of Alarms Primary Situation Mutual Aid Action Taken Primary Action Taken Secondary Action Taken Other Detector Alerted Occupants Property Use Area of Fire Origin Ignition Cause Ignition Factor Primary Ignition Factor Secondary Heat Source Item First Ignited Human Factors Associated with Ignition Structure Type Structure Status Floor of Fire Origin Fire Spread No Flame Spead Number of floors with minimum damage Number of floors with significant damage Number of floors with heavy damage Number of floors with extreme damage Detectors Present Detector Type Detector Operation Detector Effectiveness Detector Failure Reason Automatic Extinguishing System Present Automatic Extinguishing Sytem Type Automatic Extinguishing Sytem Perfomance Automatic Extinguishing Sytem Failure Reason Number of Sprinkler Heads Operating Supervisor District Neighborhood District Location Call Number Unit ID Incident Number Call Type Call Date Watch Date Received DtTm Entry DtTm Dispatch DtTm Response DtTm On Scene DtTm Transport DtTm Hospital DtTm Call Final Disposition Available DtTm Address City Zipcode of Incident Battalion Station Area Box Original Priority Priority Final Priority ALS Unit Call Type Group Number of Alarms Unit Type Unit sequence in call dispatch Fire Prevention District Supervisor District Neighborhooods - Analysis Boundaries Location RowID 16146547 0 1st St/mission Street 12/30/2016 163653973 12/30/2016 11:17:30 PM 12/30/2016 11:19:53 PM 12/31/2016 12:23:07 AM San Francisco 94105 B03 35 2126 4 14 2 3 0 0 null null null 0 0 0 0 null 311 medical assist, assist ems crew n none 32 provide basic life support (bls) null null null 963 street or road in commercial area null null null null null null null null null null null na null null null null null null null null null null null null null null 6 Financial District/South Beach (37.7897620000297, -122.397576) 1030118 E08 30625 Medical Incident 04/12/2000 04/12/2000 04/12/2000 09:27:45 PM 04/12/2000 09:28:58 PM 04/12/2000 09:29:21 PM 04/12/2000 09:31:26 PM 04/12/2000 09:32:34 PM null null Other 04/12/2000 09:45:28 PM 4TH ST/CHANNEL ST SF null B03 08 2226 3 3 3 false null 1 ENGINE 1 3 6 None (37.7750268633971, -122.392346204303) 001030118-E08 16146531 0 85 2nd Street 12/30/2016 163653792 12/30/2016 10:25:56 PM 12/30/2016 10:31:49 PM 12/30/2016 10:44:13 PM San Francisco 94105 B03 1 2145 3 10 0 0 0 0 null null null 0 0 0 0 null 735 alarm system sounded due to malfunction n none 86 investigate null null null 599 business office null null null null null null null null null null null na null null null null null null null null null null null null null null 6 Financial District/South Beach (37.7882730000297, -122.400013) 1030118 E08 30625 Medical Incident 04/12/2000 04/12/2000 04/12/2000 09:27:45 PM 04/12/2000 09:28:58 PM 04/12/2000 09:29:21 PM 04/12/2000 09:31:26 PM 04/12/2000 09:32:34 PM null null Other 04/12/2000 09:45:28 PM 4TH ST/CHANNEL ST SF null B03 08 2226 3 3 3 false null 1 ENGINE 1 3 6 None (37.7750268633971, -122.392346204303) 001030118-E08 16146501 0 410 Townsend Street 12/30/2016 163653517 12/30/2016 08:54:08 PM 12/30/2016 08:57:27 PM 12/30/2016 09:22:17 PM San Francisco 94107 B03 8 2236 3 10 0 0 0 0 null null null 0 0 0 0 null 735 alarm system sounded due to malfunction n none 86 investigate null null null 599 business office null null null null null null null null null null null na null null null null null null null null null null null null null null 6 Mission Bay (37.7751640000296, -122.397545) 1030118 E08 30625 Medical Incident 04/12/2000 04/12/2000 04/12/2000 09:27:45 PM 04/12/2000 09:28:58 PM 04/12/2000 09:29:21 